In [5]:
entities_list = [
        # {
        #     "chebi_chemical_entities": {
        #         "uri": "http://purl.obolibrary.org/obo/CHEBI",
        #         "label": "chemical entities",
        #         "description": "Chemical entities in ChEBI.",
        #         "endpoint": "https://sparql.uniprot.org/sparql/",
        #         "pagination": True,
        #         "query": """
        #                 PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
        #                 PREFIX rh:   <http://rdf.rhea-db.org/>
        #                 SELECT DISTINCT ?uri ?label
        #                 WHERE {
        #                     # Restrict to things that are recognized as Rhea reactions
        #                     ?reaction rdfs:subClassOf rh:Reaction ;
        #                             rh:side        ?side .
        #                     # Each reaction side contains one or more participants
        #                     ?side rh:contains ?participant .
        #                     # Each participant is linked to a ChEBI entity via 'rh:compound' 
        #                     ?participant rh:compound ?compound .
        #                     # 'rh:chebi' points to the ChEBI identifier (e.g., http://purl.obolibrary.org/obo/CHEBI_15377)
        #                     ?compound rh:chebi ?uri .
        #                     ?uri rdfs:label ?label .
        #                 }"""
        #     }
        # },
        # {
        #     "uniprot_disease": {
        #         "uri": "http://purl.uniprot.org/core/Disease",
        #         "label": "Disease",
        #         "description": "The preferred names of diseases.",
        #         "endpoint": "https://sparql.uniprot.org/sparql/",
        #         "pagination": True,
        #         "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
        #                     PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
        #                     PREFIX up: <http://purl.uniprot.org/core/>
        #                     SELECT ?uri ?label ?type WHERE {
        #                         ?uri a up:Disease ;
        #                             skos:prefLabel ?label .
        #                     }"""
        #     }
        # },
        {
            "uniprot_taxon": {
                "uri": "http://purl.uniprot.org/core/Taxon",
                "label": "species",
                "description": "taxon scientific names",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX up: <http://purl.uniprot.org/core/>
                            SELECT ?uri ?label
                            WHERE {
                                ?uri a up:Taxon ;
                                    up:scientificName ?label .
                            }"""
            }
        },
        # {
        #     "rhea_reaction": {
        #         "uri": "http://rdf.rhea-db.org/",
        #         "label": "reactions",
        #         "description": "Reactions in RHEA.",
        #         "endpoint": "https://sparql.uniprot.org/sparql/",
        #         "pagination": True,
        #         "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
        #                     PREFIX rh:   <http://rdf.rhea-db.org/>
        #                     SELECT DISTINCT ?uri ?label
        #                     WHERE {
        #                         ?uri rdfs:subClassOf rh:Reaction .
        #                         ?uri rdfs:label ?label .
        #                     }"""
        #     }
        # },
        
    ]

In [6]:
from endpoint_loader import *
import pandas as pd
entities = load_entities_from_endpoints(entities_list)

df = pd.DataFrame(entities)

display(df.head())

print(f"Total entities: {len(df)}")
print(f"Columns: {df.columns.tolist()}")
print(f"Entity types: {df['entity_type'].unique()}")

Flattened 1 entities for indexing
Flattened entities: [{'uri': 'http://purl.uniprot.org/core/Taxon', 'label': 'species', 'description': 'taxon scientific names', 'endpoint': 'https://sparql.uniprot.org/sparql/', 'pagination': True, 'query': 'PREFIX up: <http://purl.uniprot.org/core/>\n                            SELECT ?uri ?label\n                            WHERE {\n                                ?uri a up:Taxon ;\n                                    up:scientificName ?label .\n                            }'}]
Loading entities from https://sparql.uniprot.org/sparql/ for species...
Found 200000 entities for species in https://sparql.uniprot.org/sparql/
  Retrieved 200000 entities, total so far: 200000
Found 200000 entities for species in https://sparql.uniprot.org/sparql/
  Retrieved 200000 entities, total so far: 400000
Found 200000 entities for species in https://sparql.uniprot.org/sparql/
  Retrieved 200000 entities, total so far: 600000
Found 200000 entities for species in https:

label                                      uri  \
0     Hysteriaceae  http://purl.uniprot.org/taxonomy/100025   
1         Thomomys   http://purl.uniprot.org/taxonomy/10011   
2  Thomomys bottae   http://purl.uniprot.org/taxonomy/10013   
3     Heteromyidae   http://purl.uniprot.org/taxonomy/10015   
4     Philenoptera  http://purl.uniprot.org/taxonomy/100163   

                         endpoint_url entity_type             description  
0  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
1  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
2  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
3  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
4  https://sparql.uniprot.org/sparql/     literal  taxon scientific names

Total entities: 2614312
Columns: ['label', 'uri', 'endpoint_url', 'entity_type', 'description']
Entity types: ['literal']


In [3]:
import pickle

df.to_csv('entities_dataframe.csv', index=False)  
with open('entities_dataframe.pkl', 'wb') as f:
    pickle.dump(df, f)

In [2]:
import os
import pickle
if os.path.exists('entities_dataframe.pkl'):
    with open('entities_dataframe.pkl', 'rb') as f:
        df = pickle.load(f)
        entities = df.to_dict('records')
else:
    # Load from endpoint if file doesn't exist
    from endpoint_loader import *
    entities = load_entities_from_endpoints(entities_list)
    df = pd.DataFrame(entities)
    # Save for next time
    with open('entities_data.pkl', 'wb') as f:
        pickle.dump(df, f)

In [ ]:
from entity_indexing_pipeline_v3 import EmbeddingPipeline
import ray


ray.init(ignore_reinit_error=True)
s
pipeline = EmbeddingPipeline()
pipeline.add_documents(entities, batch_size=144)

ray.shutdown()

2025-03-29 10:39:10,837	INFO worker.py:1843 -- Started a local Ray instance. View the dashboard at http://127.0.0.1:8265 


Creating embedding workers...
Initializing Qdrant client...


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

Error loading upload log: Expecting ',' delimiter: line 1 column 19775128 (char 19775127)
Collection 'biomedical_entities' exists, skipping initialization
Adding 2650724 documents in batches of 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.075160026550293 seconds
Time taken to generate sparse embeddings with Ray Distributed Computing: 13.96476697921753 seconds
Creating points...
Uploading points...
✓ Batch 1/18408 - Total uploaded: 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.969425916671753 seconds
Time taken to generate sparse embeddings with Ray Distributed Computing: 22.855857133865356 seconds
Creating points...
Uploading points...
✓ Batch 2/18408 - Total uploaded: 288
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.8981409072875977 seconds
Time taken to generate sparse embeddings with Ray Distributed Computing: 23.256271839141846 seconds
Creating 

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x103114790>>
Traceback (most recent call last):
  File "/Users/sebastian/Documents/Bachelor Thesis/sparql-rag-agent/sparql-rag-agent/.venv/lib/python3.11/site-packages/ipykernel/ipkernel.py", line 775, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(

KeyboardInterrupt: 


Time taken to generate sparse embeddings with Ray Distributed Computing: 8.83504581451416 seconds
Creating points...
Uploading points...
✓ Batch 7/18408 - Total uploaded: 1008
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 4.275254964828491 seconds


In [5]:
ray.shutdown()

In [1]:
entities_list = [
        {
            "chebi_chemical_entities": {
                "uri": "http://purl.obolibrary.org/obo/CHEBI",
                "label": "chemical entities",
                "description": "Chemical entities in ChEBI.",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """
                        PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
                        PREFIX rh:   <http://rdf.rhea-db.org/>
                        SELECT DISTINCT ?uri ?label
                        WHERE {
                            # Restrict to things that are recognized as Rhea reactions
                            ?reaction rdfs:subClassOf rh:Reaction ;
                                    rh:side        ?side .
                            # Each reaction side contains one or more participants
                            ?side rh:contains ?participant .
                            # Each participant is linked to a ChEBI entity via 'rh:compound' 
                            ?participant rh:compound ?compound .
                            # 'rh:chebi' points to the ChEBI identifier (e.g., http://purl.obolibrary.org/obo/CHEBI_15377)
                            ?compound rh:chebi ?uri .
                            ?uri rdfs:label ?label .
                        }"""
            }
        },
        {
            "uniprot_disease": {
                "uri": "http://purl.uniprot.org/core/Disease",
                "label": "Disease",
                "description": "The preferred names of diseases.",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
                            PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
                            PREFIX up: <http://purl.uniprot.org/core/>
                            SELECT ?uri ?label ?type WHERE {
                                ?uri a up:Disease ;
                                    skos:prefLabel ?label .
                            }"""
            }
        },
        {
            "uniprot_taxon": {
                "uri": "http://purl.uniprot.org/core/Taxon",
                "label": "species",
                "description": "taxon scientific names",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX up: <http://purl.uniprot.org/core/>
                            SELECT ?uri ?label
                            WHERE {
                                ?uri a up:Taxon ;
                                    up:scientificName ?label .
                            }"""
            }
        },
        {
            "rhea_reaction": {
                "uri": "http://rdf.rhea-db.org/",
                "label": "reactions",
                "description": "Reactions in RHEA.",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
                            PREFIX rh:   <http://rdf.rhea-db.org/>
                            SELECT DISTINCT ?uri ?label
                            WHERE {
                                ?uri rdfs:subClassOf rh:Reaction .
                                ?uri rdfs:label ?label .
                            }"""
            }
        },
        
    ]

In [2]:
from endpoint_loader import *
import pandas as pd
entities = load_entities_from_endpoints(entities_list)

df = pd.DataFrame(entities)

display(df.head())
print(f"Total entities: {len(df)}")
print(f"Columns: {df.columns.tolist()}")
print(f"Entity types: {df['entity_type'].unique()}")

Flattened 4 entities for indexing
Flattened entities: [{'uri': 'http://purl.obolibrary.org/obo/CHEBI', 'label': 'chemical entities', 'description': 'Chemical entities in ChEBI.', 'endpoint': 'https://sparql.uniprot.org/sparql/', 'pagination': True, 'query': "\n                        PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>\n                        PREFIX rh:   <http://rdf.rhea-db.org/>\n                        SELECT DISTINCT ?uri ?label\n                        WHERE {\n                            # Restrict to things that are recognized as Rhea reactions\n                            ?reaction rdfs:subClassOf rh:Reaction ;\n                                    rh:side        ?side .\n                            # Each reaction side contains one or more participants\n                            ?side rh:contains ?participant .\n                            # Each participant is linked to a ChEBI entity via 'rh:compound' \n                            ?participant rh:compound 

label  \
0  2-O-(alpha-D-mannopyranosyl)-1-phosphatidyl-1D...   
1                   (3E,5Z)-tetradecadienoyl-CoA(4-)   
2                         (5Z)-tetradecenoyl-CoA(4-)   
3        (25R)-3beta-hydroxycholest-5-en-7-one-26-al   
4      (25R)-3beta-hydroxycholest-5-en-7-one-26-oate   

                                          uri  \
0  http://purl.obolibrary.org/obo/CHEBI_87673   
1  http://purl.obolibrary.org/obo/CHEBI_71586   
2  http://purl.obolibrary.org/obo/CHEBI_84650   
3  http://purl.obolibrary.org/obo/CHEBI_87677   
4  http://purl.obolibrary.org/obo/CHEBI_87678   

                         endpoint_url entity_type                  description  
0  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
1  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
2  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
3  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
4  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.

Total entities: 2650724
Columns: ['label', 'uri', 'endpoint_url', 'entity_type', 'description']
Entity types: ['literal']


In [3]:
from entity_indexing_pipeline_v3 import EmbeddingPipeline
import ray


ray.init(ignore_reinit_error=True)
#dense_model_name="BAAI/bge-base-en-v1.5"

pipeline = EmbeddingPipeline(collection_name="biomedical_entity_collection_v2.0")
pipeline.add_documents(entities, batch_size=144)

ray.shutdown()

2025-04-08 01:17:06,170	INFO worker.py:1843 -- Started a local Ray instance. View the dashboard at http://127.0.0.1:8265 


Creating embedding workers...
Initializing Qdrant client...
No existing upload log found, starting fresh
Collection 'biomedical_entity_collection_v2.0' exists, skipping initialization
Adding 2650724 documents in batches of 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.407313346862793 seconds
Creating points...
Uploading points...
✓ Batch 1/18408 - Total uploaded: 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.6625359058380127 seconds
Creating points...
Uploading points...
✓ Batch 2/18408 - Total uploaded: 288
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 2.5378828048706055 seconds
Creating points...
Uploading points...
✓ Batch 3/18408 - Total uploaded: 432
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 2.0483298301696777 seconds
Creating points...
Uploading points...
✓ Batch 4/18408 - Total uploaded: 576
Chunk size

(raylet) [2025-04-08 02:05:47,611 E 10504 40729] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-08_01-17-05_156871_8399 is over 95% full, available space: 23.0209 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.


Time taken to generate dense embeddings with Ray Distributed Computing: 0.9871459007263184 seconds
Creating points...
Uploading points...
✓ Batch 1999/18408 - Total uploaded: 287856
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.974827766418457 seconds
Creating points...
Uploading points...
✓ Batch 2000/18408 - Total uploaded: 288000
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.1011757850646973 seconds
Creating points...
Uploading points...
✓ Batch 2001/18408 - Total uploaded: 288144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.6740989685058594 seconds
Creating points...
Uploading points...
✓ Batch 2002/18408 - Total uploaded: 288288
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.9570159912109375 seconds
Creating points...
Uploading points...
✓ Batch 2003/18408 - Total uploaded: 288432
Chunk size: 36
Time taken to ge

(raylet) [2025-04-08 02:05:57,683 E 10504 40729] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-08_01-17-05_156871_8399 is over 95% full, available space: 23.0065 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.


...

Time taken to generate dense embeddings with Ray Distributed Computing: 0.9729201793670654 seconds
Creating points...
Uploading points...
✓ Batch 15897/18408 - Total uploaded: 2289168
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.7184128761291504 seconds
Creating points...
Uploading points...
✓ Batch 15898/18408 - Total uploaded: 2289312
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.8558831214904785 seconds
Creating points...
Uploading points...
✓ Batch 15899/18408 - Total uploaded: 2289456
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.7958450317382812 seconds
Creating points...
Uploading points...
✓ Batch 15900/18408 - Total uploaded: 2289600
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6147730350494385 seconds
Creating points...
Uploading points...
✓ Batch 15901/18408 - Total uploaded: 2289744
Chunk size: 36


(raylet) [2025-04-08 09:35:17,925 E 90805 521968] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-08_05-52-46_540667_8399 is over 95% full, available space: 15.3064 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.


Time taken to generate dense embeddings with Ray Distributed Computing: 0.760089635848999 seconds
Creating points...
Uploading points...
✓ Batch 15902/18408 - Total uploaded: 2289888
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.8750169277191162 seconds
Creating points...
Uploading points...
✓ Batch 15903/18408 - Total uploaded: 2290032
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.661910057067871 seconds
Creating points...
Uploading points...


KeyboardInterrupt: 

(raylet) [2025-04-08 09:35:27,963 E 90805 521968] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-08_05-52-46_540667_8399 is over 95% full, available space: 15.0007 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.
(raylet) [2025-04-08 09:35:38,049 E 90805 521968] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-08_05-52-46_540667_8399 is over 95% full, available space: 14.8794 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.
(raylet) [2025-04-08 09:35:48,144 E 90805 521968] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-08_05-52-46_540667_8399 is over 95% full, available space: 14.8194 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.
(raylet) [2025-04-08 09:35:58,157 E 90805 521968] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-08_05-52-46_540667_8399 is over 95% full, available space: 12.8201 GB; capacity: 460.432 GB. Object creation will fail i

In [4]:
import ray

ray.shutdown()